# Kamera kalibráció

A kamera kalibráció célja a kamera külső (egy adott koordinátarendszerbeli pozíció, eltolás és elforgatás) valamint belső paramétereinek (fókusztávolság, pixelek nyírása) meghatározása.

A kalibráció során az alábbi paramétereket akarjuk meghatározni:
* **Belső paraméterek:** 3D-2D leképezés a kamera koordinátarendszerből a kép koordinátarendszerbe 
  * **f**: fókusztávolság
  * **$c_x$, $c_y$**: kamera középpont, főpont
  * *disztorziós együtthatók*: a lencsetorzítást befolyásoló tényezők
* **Külső paraméterek:** a kamera koordinátarendszerek pozíciója és orientációja a világ koordinátarendszerhez képest 
  * **R**: 3D forgatási mátrix a külső koordinátarendszerben
  * **t**: 3D eltolásvektor a külső koordinátarendszerben

<img src="kamera_kalibracio/koordinata_rendszer2.png" alt="Koordinátarendszerek" width="50%" />

Legyen $q=(x,y,1)^T$ egy pixel a képkoordinátarendszerben (homogén koordinátákkal), valamint egy $Q=(X,Y,Z,1)^T$ egy pont a világ koordinátarendszerben. A két koordinátarendszer között felírhatjuk az alábbi kapcsolatot:
$$
s\begin{bmatrix}
x \\ y \\ 1
\end{bmatrix} = 
\underbrace{\begin{bmatrix}
f_x & \gamma & c_x  \\ 
0 & f_y & c_y  \\ 
0 & 0 & 1   
\end{bmatrix}}_\limits{\mathbf{K}}
[\mathbf{R} ~~ \mathbf{t}]\cdot
\begin{bmatrix}
X \\ Y \\ Z \\ 1
\end{bmatrix} 
$$
ahol az $\gamma$ paraméter a nyírási paraméter, amely négyzetes pixelek esetében 0, az $s$ pedig egy skálafaktor ugyanis ez a leképezés egy skálafaktor erejéig meghatározott. A kamera külső paraméterei az $\mathbf{R}$ egy $3\times3$-as forgatási vektor, a $\mathbf{t}$ pedig egy $3\times1$-es eltolás vektor. A $\mathbf{K}$ mátrix, amely a kamera belső paramétereit tartalmazza. 
Legyen $\mathbf{P}$ egy általános kamera mátrix, vagyis $\mathbf{P}=\mathbf{K}[\mathbf{R}|\mathbf{t}]$

Tekintsünk $N$ $\mathbf{X}_i \leftrightarrow \mathbf{x}_i$ pontmegfeleltetést, ahol $N$ a pontok számát jelöli. Valamennyi pontpárra igaz az $\mathbf{x}=\mathbf{P}\mathbf{X}_i$ összefüggés, amelyet $\mathbf{x}\times\mathbf{P}\mathbf{X}_i = \mathbf{0}$ alakban is kifejezhetünk. Ezt a kifejezést átírhatjuk az alábbi alakba, ahol a $\mathbf{P}$ mátrix 4-elemű sorvektorait $\mathbf{\Pi_1}^T$, $\mathbf{\Pi_2}^T$, $\mathbf{\Pi_3}^T$ jelöli: 
$$
\mathbf{x_i} \times \mathbf{P}\mathbf{X_i} = 
\begin{bmatrix}
\mathbf{0}^T & -x_{i3}\mathbf{X_i}^T & x_{i2}\mathbf{X_i}^T \\
x_{i3}\mathbf{X_i}^T & \mathbf{0}^T & x_{i1}\mathbf{X_i}^T \\
x_{i2}\mathbf{X_i}^T &  x_{i1}\mathbf{X_i}^T & \mathbf{0}^T \\
\end{bmatrix} \begin{pmatrix} \mathbf{\Pi_1} \\ \mathbf{\Pi_2} \\ \mathbf{\Pi_3} \end{pmatrix} 
$$
Mivel a harmadik sor kifejezhező az első kettő lineáris kombinációjaként, ezért csak két sor lesz lineárisan független és így felírhatjuk az alábbi egyenletrendszert:
$$
\mathbf{x_i} \times \mathbf{P}\mathbf{X_i} = 
\begin{bmatrix}
\mathbf{0}^T & -x_{i3}\mathbf{X_i}^T & x_{i2}\mathbf{X_i}^T \\
x_{i3}\mathbf{X_i}^T & \mathbf{0}^T & x_{i1}\mathbf{X_i}^T \\
\end{bmatrix} \begin{pmatrix} \mathbf{\Pi_1} \\ \mathbf{\Pi_2} \\ \mathbf{\Pi_3} \end{pmatrix} 
$$
Tehát $N$ pontmegfeleltetés esetén $2N$ egyenletünk lesz. 
Jelölje $\mathbf{p} = (P_{11}, \dots, P_{34})^T$ a $\mathbf{P}$ mátrix ismeretlen elemeit. Ekkor a fenti egyenletrendszert $N\ge 6$ pontpárra felírva az alábbi egyenletrendszert kapjuk
$$
\mathbf{Ap} = \mathbf{0},
$$
ahol az $\mathbf{A}$ mátrix $2N\times 12$ méretű. További feltételként előírhatjuk a $\|\mathbf{p}\|=1$ megszorítást, amellyel csökkenthető az egyenletrendszer algebrai hibája. Az egyenletrendszer megoldását az $A$ mátrix SVD felbontásával kapjuk. 




## A kamera kalibráció lépései 

A lépéseket és a matematikai hátteret lásd a [jegyzetben](kamera_kalibracio/kato_czuni_szamitogepes_latas0816.pdf).

1. Készítsünk képeket egy tetszőleges kamerával egy [sakktáblamintáról](kamera_kalibracio/pattern.png)!
> Ügyeljünk arra, hogy a minta (a fehér szélét is beleértve) teljesen látszódjon! Ne csak szemből, hanem oldalsó, meredek beesési szögekből is fényképezzük le a mintát, hogy a lencse torzítása minél inkább megmutatkozzon. Ügyeljünk arra, hogy a minta sík felületen legyen, ennek érdekében egy teljesképernyős képként is kitehetjük a monitorra. 
2. Mérjük le a valódi méretű négyzetek oldalhosszát!
3. Adjuk meg a programnak, hogy hány darab sort és oszlopot kell találnia mintán, valamint adjuk meg ezeknek a négyzeteknek a méretét (amit a 2. pontban lemértünk). Ezzel egy ideális rácsot állítunk elő.  
4. Minden egyes képen határozzuk meg a sakktábla minta sarokpontjait és párosítsuk ezen "torz" rács pontjait az ideális rácspontokhoz. 
5. Határozzuk meg a $\mathbf{P}$ általános kamera mátrixot a *Gold Standard* algoritmussal.
  1. Normalizáljuk az $\mathbf{X_i}$ és $\mathbf{x_i}$ pontok koordinátáit. 
  2. A normalizált pontkoordinátákból konstruált $\mathbf{Ap=0}$, $\|\mathbf{p}\|=1$ egyenletrendszer megoldását az $\mathbf{A}$ mátrix legkisebb szinguláris értékéhez tartozó egységnyi normájú szinguláris vektora adja, amelyet az $\mathbf{A}$ mátrix SVD felbontásával kapunk meg. 
  3. Az előző lépésben kapott megoldást kezdeti értéknek használva minimalizáljuk az 
  $$
      \sum_i \|\mathbf{x_i} - \mathbf{PX_i}\|^2
  $$
  képlettel megadott geometriai hibát a *Levenberg-Marquardt* algoritmussal. 
  4. Az előző lépésben kapott $\mathbf{P'}$ megoldásból a keresett kameramátrixot denormalizálással kapjuk. 